# Virtual Sensing - Linear Regression

In [1]:
# libraries
import datetime
from datetime import date, timedelta
from os import path
import pandas as pd
import numpy as np
import statistics
import boto3
import s3fs
import sys
from fastparquet import ParquetFile
from sklearn import linear_model
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.preprocessing import StandardScaler

import warnings
warnings.filterwarnings('ignore')

pd.set_option('display.max_columns', 500)

In [2]:
# constants
sys.path.append("../HistoricalData/")
from getData import get_data

UP_LEFT = (38.008050, -122.536985)    
UP_RIGHT = (38.008050, -122.186437)   
DOWN_RIGHT = (37.701933, -122.186437) 
DOWN_LEFT = (37.701933, -122.536985)  
START_DATE = '2019/01/01' 
END_DATE = '2019/09/30'   
START_HOUR = '0'        
END_HOUR = '24'   

In [3]:
# load data into dataframe
data_df = get_data(UP_LEFT, UP_RIGHT, DOWN_RIGHT, DOWN_LEFT, START_DATE, END_DATE, START_HOUR, END_HOUR, 'Monthly')

In [4]:
# get rid of rows that have no wind data? uncomment if yes.
# data_df = data_df[data_df.wind_data == 1.0]

In [5]:
# should be (726292, 68)
data_df.shape

(726292, 68)

In [10]:
# add elevation data
elev_df = pd.read_csv('sensor_elevations.csv', header='infer', float_precision='high')
elev_df = elev_df.drop(columns='resolution')
data_df = pd.merge(data_df, elev_df)
print("How many elevations are missing?", result_df.elevation.isna().sum())
print("Shape of the new dataframe:", result_df.shape)

How many elevations are missing? 0
Shape of the new dataframe: (723606, 69)


Some data gets dropped because floating point doesn't quite match on sensor '23927' 

In [11]:
# winnow down the features
columns_to_keep = ['created', 'lat', 'lon', 'wind_data', 'wind_direction', 'wind_speed', 'gusts', 'gust_speed', 
                   'variable_winds', 'variable_wind_info', 'epa_pm25_value', 'wkday', 
                   'daytype', 'timeofday', 'wind_compass', 'temperature', 'humidity', 'elevation']
X_data_df = data_df[columns_to_keep]
y_data_df = data_df['2_5um']

In [12]:
# fix datatyping
X_data_df.dtypes

created                 int64
lat                   float64
lon                   float64
wind_data             float32
wind_direction         object
wind_speed            float64
gusts                 float32
gust_speed            float64
variable_winds        float32
variable_wind_info     object
epa_pm25_value        float64
wkday                  object
daytype                object
timeofday              object
wind_compass           object
temperature           float64
humidity              float64
elevation             float64
dtype: object

In [13]:
X_data_df.wind_data = X_data_df.wind_data.astype(bool)
X_data_df.variable_winds = X_data_df.variable_winds.astype(bool)
X_data_df.gusts = X_data_df.gusts.astype(bool)
X_data_df.daytype = X_data_df.daytype.astype(str)
X_data_df.daytype = X_data_df.daytype.astype('category')
X_data_df.timeofday = X_data_df.timeofday.astype(str)
X_data_df.timeofday = X_data_df.timeofday.astype('category')
X_data_df.wind_compass = X_data_df.wind_compass.astype(str)
X_data_df.wind_compass = X_data_df.wind_compass.astype('category')
X_data_df.wkday = pd.to_numeric(X_data_df.wkday)
X_data_df.wkday = X_data_df.wkday.astype('category')

In [14]:
# handle variable winds missing values 
vrb_wind_range_readings = 0
mid_ranges = list()

for row in range(len(X_data_df)):
    if X_data_df.variable_winds.iloc[row]:
        info = X_data_df.variable_wind_info.iloc[row]
        if info:
            vrb_wind_range_readings += 1
            first, second = info.split('V')
            mid_range = int((int(first) + int(second)) / 2)
            if (X_data_df.wind_direction.iloc[row] == 'VRB'):
                X_data_df.wind_direction.lloc[row] = mid_range
            mid_ranges.append(mid_range)

replacement = statistics.mode(mid_ranges)
X_data_df = X_data_df.replace('VRB', replacement) # give variable wind the most frequent midpoint variable range
X_data_df = X_data_df.drop(columns = ['variable_wind_info'])

In [15]:
# handle missing wind values with means 
wind_direction_obs = pd.to_numeric(X_data_df.wind_direction.dropna())
wind_direction_avg = wind_direction_obs.mean()
wind_direction_avg = int(wind_direction_avg)
X_data_df.wind_direction = X_data_df.wind_direction.replace(np.nan, wind_direction_avg) # give missing wind direction the mean
X_data_df.wind_direction = X_data_df.wind_direction.replace('', wind_direction_avg)
X_data_df.wind_direction = X_data_df.wind_direction.astype(int)
wind_speed_obs = pd.to_numeric(X_data_df.wind_speed.dropna())
wind_speed_avg = wind_speed_obs.mean()
X_data_df.wind_speed = X_data_df.wind_speed.replace(np.nan, wind_speed_avg) # give missing wind speed the mean
X_data_df.wind_speed = X_data_df.wind_speed.replace('', wind_speed_avg)
X_data_df.gust_speed = X_data_df.gust_speed.replace(np.nan, 0)
X_data_df.gust_speed = X_data_df.gust_speed.replace('', 0)
X_data_df.epa_pm25_value = X_data_df.epa_pm25_value.replace(np.nan, X_data_df.epa_pm25_value.mean())
X_data_df.temperature = X_data_df.temperature.replace(np.nan, X_data_df.temperature.mean())
X_data_df.humidity = X_data_df.humidity.replace(np.nan, X_data_df.humidity.mean())

In [16]:
# one hot encode the categoricals
X_data_df = pd.concat([X_data_df,pd.get_dummies(X_data_df['timeofday'], prefix='timeofday')],axis=1)
X_data_df = pd.concat([X_data_df,pd.get_dummies(X_data_df['daytype'], prefix='daytype')], axis=1)
X_data_df = pd.concat([X_data_df,pd.get_dummies(X_data_df['wind_compass'], prefix='compass')], axis=1)

In [17]:
# remove the original columns that got one hot encoded, type the one hots as bools
X_data_df = X_data_df.drop(columns=['timeofday','daytype','wind_compass'])
X_data_df.timeofday_afternoon = X_data_df.timeofday_afternoon.astype(bool)
X_data_df.timeofday_evening = X_data_df.timeofday_evening.astype(bool)
X_data_df.timeofday_morning = X_data_df.timeofday_morning.astype(bool)
X_data_df.timeofday_night = X_data_df.timeofday_night.astype(bool)
X_data_df.daytype_Weekday = X_data_df.daytype_Weekday.astype(bool)
X_data_df.daytype_Weekend = X_data_df.daytype_Weekend.astype(bool)
X_data_df.compass_ERROR = X_data_df.compass_ERROR.astype(bool)
X_data_df.compass_East = X_data_df.compass_East.astype(bool)
X_data_df.compass_Missing = X_data_df.compass_Missing.astype(bool)
X_data_df['compass_No wind'] = X_data_df['compass_No wind'].astype(bool)
X_data_df.compass_North = X_data_df.compass_North.astype(bool)
X_data_df.compass_South = X_data_df.compass_South.astype(bool)
X_data_df.compass_West = X_data_df.compass_West.astype(bool)

In [18]:
# let's see again where we are at
X_data_df.dtypes

created                  int64
lat                    float64
lon                    float64
wind_data                 bool
wind_direction           int64
wind_speed             float64
gusts                     bool
gust_speed             float64
variable_winds            bool
epa_pm25_value         float64
wkday                    int64
temperature            float64
humidity               float64
elevation              float64
timeofday_afternoon       bool
timeofday_evening         bool
timeofday_morning         bool
timeofday_night           bool
daytype_Weekday           bool
daytype_Weekend           bool
compass_ERROR             bool
compass_East              bool
compass_Missing           bool
compass_No wind           bool
compass_North             bool
compass_South             bool
compass_West              bool
dtype: object

In [19]:
# confirm no NAs at this point
for col in X_data_df.columns:
    testy = X_data_df[col]
    print(col, testy.isna().sum())

created 0
lat 0
lon 0
wind_data 0
wind_direction 0
wind_speed 0
gusts 0
gust_speed 0
variable_winds 0
epa_pm25_value 0
wkday 0
temperature 0
humidity 0
elevation 0
timeofday_afternoon 0
timeofday_evening 0
timeofday_morning 0
timeofday_night 0
daytype_Weekday 0
daytype_Weekend 0
compass_ERROR 0
compass_East 0
compass_Missing 0
compass_No wind 0
compass_North 0
compass_South 0
compass_West 0


In [65]:
# experimenting: just keep the continuous variables
columns_to_keep = ['created', 'lat', 'lon', 'epa_pm25_value', 'wkday', 'temperature', 'humidity', 'elevation', 'compass_East', 'compass_North', 'compass_South', 'compass_West', 'compass_No wind']  #'wind_direction', 'wind_speed', 
Xex_data_df = X_data_df[columns_to_keep]

In [66]:
# standardize the data
scaler = StandardScaler(copy=True, with_mean=True, with_std=True)
scaler.fit(Xex_data_df)
Xex_data_df = scaler.transform(Xex_data_df)

In [67]:
# split data into train-dev-test
X_train_and_dev, X_test, y_train_and_dev, y_test = train_test_split(Xex_data_df, y_data_df, test_size=0.20, random_state=42)
X_train, X_dev, y_train, y_dev = train_test_split(X_train_and_dev, y_train_and_dev, test_size=0.125, random_state=42)

In [68]:
# fit the data
regr = linear_model.LinearRegression(normalize = False)
regr.fit(X_train, y_train)

LinearRegression(copy_X=True, fit_intercept=True, n_jobs=None, normalize=False)

In [69]:
# make predictions
y_pred = regr.predict(X_dev)

In [70]:
# calculate accuracy
print('Coefficients: \n', regr.coef_)
# The mean squared error
print("Mean squared error: %.2f"
      % mean_squared_error(y_dev, y_pred))
# Explained variance score: 1 is perfect prediction
print('Variance (R2) score: %.2f' % r2_score(y_dev, y_pred))

Coefficients: 
 [ 0.21477705 -0.44769433 -0.4546294   0.85744086  0.12841333 -0.24660719
  0.84957134 -0.19625578 -0.02857577  0.04555318 -0.04058627 -0.0874612
  0.00725243]
Mean squared error: 39.15
Variance (R2) score: 0.05


In [71]:
for row in range(len(y_dev)):
    print("Predicted reading", y_pred[row], ". Actual reading", y_dev.iloc[row])

Predicted reading 1.9118309336243526 . Actual reading 3.54
Predicted reading 5.355665567491931 . Actual reading 4.21
Predicted reading 4.044647019224847 . Actual reading 0.18
Predicted reading 3.64970622787382 . Actual reading 0.87
Predicted reading 4.608172702657229 . Actual reading 3.03
Predicted reading 2.731346248226043 . Actual reading 2.8
Predicted reading 3.4732662603103837 . Actual reading 5.52
Predicted reading 5.314808701159816 . Actual reading 1.37
Predicted reading 6.381948155095106 . Actual reading 10.24
Predicted reading 4.4119296971514 . Actual reading 8.43
Predicted reading 3.78991279642205 . Actual reading 2.39
Predicted reading 3.7726447951776483 . Actual reading 2.31
Predicted reading 4.464326390525176 . Actual reading 1.78
Predicted reading 2.6979410900247762 . Actual reading 3.38
Predicted reading 5.749589665780613 . Actual reading 2.44
Predicted reading 3.628782641072438 . Actual reading 6.78
Predicted reading 4.501064009178475 . Actual reading 9.68
Predicted read

Predicted reading 3.593778274428446 . Actual reading 4.06
Predicted reading 4.446749084590963 . Actual reading 2.25
Predicted reading 4.796491359631348 . Actual reading 6.42
Predicted reading 4.893769015409734 . Actual reading 3.66
Predicted reading 2.8291824752412222 . Actual reading 2.34
Predicted reading 5.397438682876807 . Actual reading 2.94
Predicted reading 6.666894102184722 . Actual reading 0.84
Predicted reading 1.2494475151006514 . Actual reading 0.85
Predicted reading 3.6030639200418744 . Actual reading 2.12
Predicted reading 0.7377402398504342 . Actual reading 1.68
Predicted reading 7.311576322841457 . Actual reading 1.25
Predicted reading 5.55609369489666 . Actual reading 1.06
Predicted reading 6.594631137892765 . Actual reading 7.71
Predicted reading 2.6309834057035815 . Actual reading 5.54
Predicted reading 4.068553244118833 . Actual reading 3.88
Predicted reading 5.85606834405835 . Actual reading 6.96
Predicted reading 3.9340198891368146 . Actual reading 3.94
Predicted 

Predicted reading 2.8787293019111746 . Actual reading 5.24
Predicted reading 5.0384346912736255 . Actual reading 4.44
Predicted reading 2.188343252468913 . Actual reading 7.25
Predicted reading 4.015065351907224 . Actual reading 3.5
Predicted reading 5.3561612286011835 . Actual reading 13.1
Predicted reading 2.2061556610231814 . Actual reading 1.68
Predicted reading 4.074465449062621 . Actual reading 2.45
Predicted reading 3.02263303211713 . Actual reading 5.49
Predicted reading 3.4909796203059686 . Actual reading 5.37
Predicted reading 3.5014113488981256 . Actual reading 0.0
Predicted reading 3.773421878161342 . Actual reading 3.42
Predicted reading 3.701666543808367 . Actual reading 3.6
Predicted reading 7.163226702759074 . Actual reading 4.04
Predicted reading 4.560083210252954 . Actual reading 5.09
Predicted reading 4.305307154661719 . Actual reading 0.93
Predicted reading 3.5948755780567603 . Actual reading 1.63
Predicted reading 4.662974514270966 . Actual reading 2.54
Predicted r

Predicted reading 4.197447457940723 . Actual reading 5.32
Predicted reading 5.411754252864423 . Actual reading 3.53
Predicted reading 5.473393726962868 . Actual reading 2.03
Predicted reading 4.98843140043697 . Actual reading 19.71
Predicted reading 3.427495231432176 . Actual reading 0.82
Predicted reading 3.6039330751053713 . Actual reading 5.51
Predicted reading 4.106789174622368 . Actual reading 2.17
Predicted reading 4.430555530321222 . Actual reading 2.06
Predicted reading 5.416170400078327 . Actual reading 4.84
Predicted reading 4.159775370341 . Actual reading 2.21
Predicted reading 3.973864943615329 . Actual reading 4.93
Predicted reading 5.1327587262456165 . Actual reading 4.39
Predicted reading 0.9697138951385043 . Actual reading 4.31
Predicted reading 4.270804849075043 . Actual reading 6.93
Predicted reading 2.203371910243659 . Actual reading 2.16
Predicted reading 3.6234105774968954 . Actual reading 1.54
Predicted reading 4.0112650884013075 . Actual reading 0.71
Predicted re

Predicted reading 2.9370001637372036 . Actual reading 2.74
Predicted reading 2.968159909038607 . Actual reading 6.17
Predicted reading 2.6194407456106745 . Actual reading 1.83
Predicted reading 4.701095344279374 . Actual reading 3.92
Predicted reading 2.922766583677507 . Actual reading 1.9
Predicted reading 1.0306055086139914 . Actual reading 0.46
Predicted reading 3.9097485558638603 . Actual reading 1.0
Predicted reading 1.8610147990131982 . Actual reading 3.4
Predicted reading 4.913121825678635 . Actual reading 6.4
Predicted reading 6.992597444655898 . Actual reading 28.88
Predicted reading 3.168740289584542 . Actual reading 1.9
Predicted reading 5.592319428083852 . Actual reading 6.14
Predicted reading 4.330570656085388 . Actual reading 3.32
Predicted reading 3.910670298009062 . Actual reading 1.19
Predicted reading 5.2364310352272 . Actual reading 1.68
Predicted reading 4.895945969771967 . Actual reading 10.71
Predicted reading 4.403409407995792 . Actual reading 9.82
Predicted read

...

Predicted reading 4.254070838332215 . Actual reading 2.31
Predicted reading 2.2041395523260507 . Actual reading 0.72
Predicted reading 3.424635260467932 . Actual reading 0.44
Predicted reading 4.56088635292791 . Actual reading 6.58
Predicted reading 6.037134223208839 . Actual reading 7.62
Predicted reading 3.5724345254438443 . Actual reading 7.29
Predicted reading 3.1941084258318346 . Actual reading 1.43
Predicted reading 4.635225635775716 . Actual reading 0.71
Predicted reading 6.02575606705191 . Actual reading 5.68
Predicted reading 5.638468635667147 . Actual reading 8.29
Predicted reading 6.48773872532331 . Actual reading 8.39
Predicted reading 3.8670227143948463 . Actual reading 5.51
Predicted reading 5.692597280215738 . Actual reading 1.58
Predicted reading 4.572214100861372 . Actual reading 0.0
Predicted reading 3.8240964602927847 . Actual reading 1.29
Predicted reading 4.213520085423476 . Actual reading 3.42
Predicted reading 4.491588892015712 . Actual reading 2.96
Predicted rea

Predicted reading 5.208445563062657 . Actual reading 6.03
Predicted reading 2.0818282819607328 . Actual reading 6.22
Predicted reading 5.063895715723433 . Actual reading 6.89
Predicted reading 3.587042431817364 . Actual reading 3.03
Predicted reading 5.211964535784013 . Actual reading 4.19
Predicted reading 4.248489368357888 . Actual reading 1.31
Predicted reading 5.1835828344875425 . Actual reading 0.0
Predicted reading 2.2757486128466335 . Actual reading 5.42
Predicted reading 6.601448357188125 . Actual reading 2.16
Predicted reading 4.878290339625742 . Actual reading 4.14
Predicted reading 1.1729533212372871 . Actual reading 7.42
Predicted reading 2.7407273155009717 . Actual reading 4.07
Predicted reading 4.452834193528605 . Actual reading 11.86
Predicted reading 4.505281294219995 . Actual reading 3.6
Predicted reading 5.066067333291962 . Actual reading 6.65
Predicted reading 3.6186696680835246 . Actual reading 0.64
Predicted reading 5.299478996249954 . Actual reading 3.66
Predicted

Predicted reading 4.085373478952794 . Actual reading 0.33
Predicted reading 2.685465349771258 . Actual reading 0.25
Predicted reading 1.4007653238778421 . Actual reading 2.24
Predicted reading 4.37587373207447 . Actual reading 0.86
Predicted reading 4.43269728733128 . Actual reading 3.47
Predicted reading 5.298731819509378 . Actual reading 5.46
Predicted reading 2.2851320676125875 . Actual reading 1.68
Predicted reading 2.4839762019942775 . Actual reading 4.44
Predicted reading 4.410770904859767 . Actual reading 2.9
Predicted reading 3.5642845048962117 . Actual reading 4.39
Predicted reading 4.059422953549934 . Actual reading 6.41
Predicted reading 3.3797787763194846 . Actual reading 1.99
Predicted reading 3.560139939719379 . Actual reading 8.32
Predicted reading 6.8591654572831064 . Actual reading 2.48
Predicted reading 2.2126395630312685 . Actual reading 2.31
Predicted reading 3.241875082811511 . Actual reading 3.38
Predicted reading 5.244983434590502 . Actual reading 9.7
Predicted r

Predicted reading 3.3449617614634994 . Actual reading 3.17
Predicted reading 1.815122116065628 . Actual reading 3.48
Predicted reading 4.761236831069753 . Actual reading 10.82
Predicted reading 4.746659265226118 . Actual reading 3.34
Predicted reading 5.316981818181788 . Actual reading 2.88
Predicted reading 2.292315600502888 . Actual reading 1.24
Predicted reading 3.475236947393107 . Actual reading 2.82
Predicted reading 3.562038977713947 . Actual reading 0.58
Predicted reading 5.540500858809316 . Actual reading 3.15
Predicted reading 5.030721534926112 . Actual reading 1.27
Predicted reading 6.269981959515869 . Actual reading 9.31
Predicted reading 5.339850888443567 . Actual reading 7.11
Predicted reading 2.8813073188300438 . Actual reading 0.71
Predicted reading 6.257752465258761 . Actual reading 4.75
Predicted reading 6.87471223160525 . Actual reading 4.23
Predicted reading 2.014240544229888 . Actual reading 0.0
Predicted reading 2.3679347287338466 . Actual reading 0.69
Predicted re

Predicted reading 5.344379292078148 . Actual reading 6.2
Predicted reading 7.375318246855047 . Actual reading 1.63
Predicted reading 6.262851822997627 . Actual reading 0.36
Predicted reading 5.072560819604018 . Actual reading 1.42
Predicted reading 3.0220773252065567 . Actual reading 0.76
Predicted reading 3.7808350097869767 . Actual reading 3.31
Predicted reading 5.1862239261318965 . Actual reading 5.06
Predicted reading 5.408520020275579 . Actual reading 4.22
Predicted reading 2.31236464730138 . Actual reading 0.83
Predicted reading 3.7843097274482025 . Actual reading 6.0
Predicted reading 1.4560021061884458 . Actual reading 0.74
Predicted reading 4.654977568256878 . Actual reading 4.52
Predicted reading 4.33810467786199 . Actual reading 3.47
Predicted reading 3.182414984165475 . Actual reading 4.35
Predicted reading 6.634932024966248 . Actual reading 2.54
Predicted reading 5.277998655248586 . Actual reading 5.44
Predicted reading 3.96764899890562 . Actual reading 3.94
Predicted read

In [ ]:
# notes